In [86]:
!uv add pandas requests openai dotenv openpyxl

Resolved 118 packages in 386ms                                       
Prepared 2 packages in 124ms                                             
Installed 2 packages in 5ms                                 
 + et-xmlfile==2.0.0
 + openpyxl==3.1.5


In [9]:
import os
import dotenv
import openai
import sqlite3
import pandas as pd

dotenv.load_dotenv() # Copy .env.example to .env and fill in the blanks

oai_token = os.getenv("OPENAI_API_KEY")

oai = openai.OpenAI(api_key=oai_token)
onet = sqlite3.connect("onet.database") # Run ./create_onet_database.sh to create it
# This dataset comes from https://epoch.ai/gradient-updates/consequences-of-automating-remote-work
# It contains labels for whethere a O*NET task can be done remotely or not (labeled by GPT-4o)
# You can download it here: https://drive.google.com/file/d/1GrHhuYIgaCCgo99dZ_40BWraz-fzo76r/view?usp=sharing
df_remote_status = pd.read_csv("epoch_task_data.csv")

# BLS OEWS: https://www.bls.gov/oes/special-requests/oesm23nat.zip
df_oesm = pd.read_excel("oesm23national.xlsx")

# Run uv run enrich_task_ratings.py to get this file (trs = Task RatingS)
df_enriched_trs = pd.read_json("task_ratings_enriched.json")

In [3]:
FREQUENCY_MAP = {
    'frequency_category_1': "Yearly or less",
    'frequency_category_2': "More than yearly",
    'frequency_category_3': "More than monthly",
    'frequency_category_4': "More than weekly",
    'frequency_category_5': "Daily",
    'frequency_category_6': "Several times daily",
    'frequency_category_7': "Hourly or more"
}

In [4]:
background_prompt = '''
Estimate the typical duration to complete *one instance* of the following job task from the moment a person starts to work on it to the last moment the person will need to keep it in mind

Take into account that there might be delays between the steps to complete the task, which would lengthen the estimate.

Output a range with the format [duration A] - [duration B] where [duration A] and [duration B] correspond to one of the durations below:
- less than 30 minutes
- 30 minutes
- 1 hour
- 4 hours
- 8 hours
- 16 hours
- 3 days
- 1 week
- 3 weeks
- 6 weeks
- 3 months
- 6 months
- 1 year
- 3 years
- more than 3 year

**Do not output anything besides the range**
'''

In [11]:
df_oesm_detailed = df_oesm[df_oesm['O_GROUP'] == 'detailed'][['OCC_CODE', 'TOT_EMP', 'H_MEAN', 'A_MEAN']].copy()
df_enriched_trs['occ_code_join'] = df_enriched_trs['onetsoc_code'].str[:7]
df_merged = pd.merge(
    df_enriched_trs,
    df_oesm_detailed,
    left_on='occ_code_join',
    right_on='OCC_CODE',
    how='left'
)
df_merged = df_merged.drop(columns=['occ_code_join'])

In [12]:

df_merged = pd \
    .merge(left=df_enriched_trs, right=df_remote_status[['O*NET-SOC Code', 'Remote']], how='left', left_on='onetsoc_code', right_on='O*NET-SOC Code') \
    .drop(columns=['O*NET-SOC Code']) \
    .rename(columns={'Remote': 'remote'}) \
    .rename(columns=FREQUENCY_MAP) \
    .query('remote == "remote" and importance_average >= 3')

row = df_merged.iloc[30000]
print('Task: ', row['task'])
print('Occupation Description: ', row['occupation_description'])
print('Occupation Title: ', row['occupation_title'])

row

Task:  Develop or recommend network security measures, such as firewalls, network security audits, or automated security probes.
Occupation Description:  Design and implement computer and information networks, such as local area networks (LAN), wide area networks (WAN), intranets, extranets, and other data communications networks. Perform network modeling, analysis, and planning, including analysis of capacity needs for network infrastructures. May also design network and computer security measures. May research and recommend network and data communications hardware and software.
Occupation Title:  Computer Network Architects


onetsoc_code                                                     15-1241.00
task_id                                                               18971
task                      Develop or recommend network security measures...
occupation_title                                Computer Network Architects
occupation_description    Design and implement computer and information ...
Yearly or less                                                          0.0
More than yearly                                                       30.0
More than monthly                                                      15.0
More than weekly                                                       20.0
Daily                                                                  15.0
Several times daily                                                    15.0
Hourly or more                                                          5.0
importance_average                                                     4.35
relevance_av

In [13]:
# Cross-reference woth BLS OEWS
# It doesn't really make sens to have it per-task, we only need it per-occupation...
df_oesm_detailed = df_oesm[df_oesm['O_GROUP'] == 'detailed'][['OCC_CODE', 'TOT_EMP', 'H_MEAN', 'A_MEAN']].copy()
df_merged['occ_code_join'] = df_merged['onetsoc_code'].str[:7]
df_merged = pd.merge(
    df_merged,
    df_oesm_detailed,
    left_on='occ_code_join',
    right_on='OCC_CODE',
    how='left'
)
df_merged = df_merged.drop(columns=['occ_code_join'])
df_merged

onetsoc_code  task_id  \
0        11-1011.00     8823   
1        11-1011.00     8823   
2        11-1011.00     8823   
3        11-1011.00     8823   
4        11-1011.00     8823   
...             ...      ...   
127653   53-7121.00    12807   
127654   53-7121.00    12804   
127655   53-7121.00    12803   
127656   53-7121.00    12805   
127657   53-7121.00    12810   

                                                     task  \
0       Direct or coordinate an organization's financi...   
1       Direct or coordinate an organization's financi...   
2       Direct or coordinate an organization's financi...   
3       Direct or coordinate an organization's financi...   
4       Direct or coordinate an organization's financi...   
...                                                   ...   
127653  Unload cars containing liquids by connecting h...   
127654  Clean interiors of tank cars or tank trucks, u...   
127655  Lower gauge rods into tanks or read meters to ...   
127656  Operate conveyors and equipment to transfer gr...   
127657  Perform general warehouse activities, such as ...   

                         occupation_title  \
0                        Chief Executives   
1                        Chief Executives   
2                        Chief Executives   
3                        Chief Executives   
4                        Chief Executives   
...                                   ...   
127653  Tank Car, Truck, and Ship Loaders   
127654  Tank Car, Truck, and Ship Loaders   
127655  Tank Car, Truck, and Ship Loaders   
127656  Tank Car, Truck, and Ship Loaders   
127657  Tank Car, Truck, and Ship Loaders   

                                   occupation_description  Yearly or less  \
0       Determine and formulate policies and provide o...            5.92   
1       Determine and formulate policies and provide o...            5.92   
2       Determine and formulate policies and provide o...            5.92   
3       Determine and formulate policies and provide o...            5.92   
4       Determine and formulate policies and provide o...            5.92   
...                                                   ...             ...   
127653  Load and unload chemicals and bulk solids, suc...            6.05   
127654  Load and unload chemicals and bulk solids, suc...            1.47   
127655  Load and unload chemicals and bulk solids, suc...            4.52   
127656  Load and unload chemicals and bulk solids, suc...            6.97   
127657  Load and unload chemicals and bulk solids, suc...            5.91   

        More than yearly  More than monthly  More than weekly  Daily  \
0                  15.98              29.68             21.18  19.71   
1                  15.98              29.68             21.18  19.71   
2                  15.98              29.68             21.18  19.71   
3                  15.98              29.68             21.18  19.71   
4                  15.98              29.68             21.18  19.71   
...                  ...                ...               ...    ...   
127653             29.21               6.88             13.95  27.65   
127654              6.33              21.70             25.69  32.35   
127655              1.76               4.65             17.81  37.42   
127656             12.00               2.52              5.90  35.48   
127657             10.85               6.46             14.46  34.14   

        Several times daily  Hourly or more  importance_average  \
0                      4.91            2.63                4.52   
1                      4.91            2.63                4.52   
2                      4.91            2.63                4.52   
3                      4.91            2.63                4.52   
4                      4.91            2.63                4.52   
...                     ...             ...                 ...   
127653                 7.93            8.34                4.08   
127654                

In [76]:
response = oai.chat.completions.create(messages=[{"role": "user", "content": "Tell me a joke"}], model="gpt-4.1-2025-04-14", max_tokens=100, temperature=0.7, n=1, stop=None)
joke = response.choices[0].message.content.strip()
print(joke)

Why did the scarecrow win an award?

Because he was outstanding in his field!
